In [ ]:
import torch
import json
import os.path as osp
from math import sqrt
import numpy as np

import torch
import torch.nn.functional as F
from rdkit import Chem

from torch_geometric.loader import DataLoader
from torch_geometric.datasets import MoleculeNet
from torch_geometric.nn.models import AttentiveFP

import os
import os.path as osp
import re

import torch
import torch.nn.functional as F
from rdkit import Chem
from torch_geometric.data import (InMemoryDataset, Data, download_url,
                                  extract_gz)
from torch_geometric.loader import DataLoader
from torch_geometric.datasets import MoleculeNet
from torch_geometric.nn.models import AttentiveFP

from model import GNN,GNN_graphpred
from dataset import LSSInhibitor,GenAtomFeatures,GenAttentiveFeatures
from loss import ada_batch_all_triplet_loss
from splitters import scaffold_split, random_split, random_scaffold_split, cv_random_split


device = 'cuda:7'
batch_size = 16
epochs = 200
lr = 0.0001
decay = 1e-3
num_layer = 5
emb_dim = 300
dropout_ratio = 0
JK = 'last'
dataset = 'EAAT3'
output_model_file = ''
gnn_type = 'gin'
seed = 0
num_workers = 8
mode = 'ada_batch_all_triplet_loss'   #ada_batch_all_triplet_loss,ada_batch_hard_triplet_loss,triplet_loss
feature_type = 'custom'  #random,onehot,custom,pseudo
graph_pooling = 'set2set2' #mean,last,sum,set2set,atention


def train():
    total_loss = total_examples = 0
    for data in train_loader:
        data = data.to(device)
        optimizer.zero_grad()
        '''
        data.x = data.x.to(torch.float32)
        data.edge_index=data.edge_index.to(torch.long)
        data.edge_attr=data.edge_attr.to(torch.float32)
        data.batch=data.batch.to(torch.long)
        '''
        #out = model(float(data.x), data.edge_index.to(torch.long), data.edge_attr.to(torch.float32), data.batch.to(torch.long))
        emb,pre = model(data.x, data.edge_index, data.edge_attr, data.batch)

        #loss = F.mse_loss(out, data.y)
        loss = ada_batch_all_triplet_loss(embeddings=emb, labels=data.y, prediction=pre, device=device, minv=minv, maxv=maxv, weight=0.5, cliff=1.5,squared=False)
        loss.backward()
        optimizer.step()
        total_loss += float(loss) * data.num_graphs
        total_examples += data.num_graphs
    return sqrt(total_loss / total_examples)


@torch.no_grad()
def test(loader):
    mse = []
    for data in loader:
        data = data.to(device)
        emb,pre = model(data.x.to(torch.float32), data.edge_index, data.edge_attr, data.batch)
        pre = pre*(maxv-minv)+minv
        mse.append(F.mse_loss(pre, data.y, reduction='none').cpu())
        #print('mse:',mse)
    return float(torch.cat(mse, dim=0).mean().sqrt())


best_result_allset = []
for dataset_name in LSSInhibitor.names.keys():
    
    print(dataset_name + "\n")
    path = './data'
    
    # use the attentiveFP node and edge features during the mol-2-graph transoformation
    dataset = LSSInhibitor(path, name=dataset_name, pre_transform=GenAtomFeatures('custom')).shuffle()
    #dataset = LSSInhibitor(path, name=dataset_name, pre_transform=GenAttentiveFeatures()).shuffle()
    #dataset = MoleculeNet(path, name='FreeSolv', pre_transform=GenFeatures()).shuffle()
    print(dataset.__dict__)
    
    #get min&max for normalization
    minv = 1e12
    maxv = -1e12
    for i in dataset:
        if i.y<minv:
            minv = i.y.item()
        if i.y>maxv:
            maxv = i.y.item()
    print(f'minv:{minv}  maxv:{maxv}') 
    
    
    # cross validation splitting
    cv_random_split(dataset, data_name = dataset_name, fold_idx = 0, frac_train=0.8, frac_valid=0.2, seed=0,smiles_list=None)
    if os.path.isfile(dataset_name+'_split_folds.json'):
        with open(dataset_name+"_split_folds.json","r") as f:
            folds_dict = json.load(f)
            print('FOLDS_dict:',folds_dict)
    '''
    N = len(dataset) // 5
    val_dataset = dataset[:N]
    test_dataset = dataset[N:2 * N]
    train_dataset = dataset[2 * N:]
    '''
    best_result = []
    
    for fold in range(len(folds_dict)):
        
        train_dataset = dataset[folds_dict[str(fold)]['train']]
        test_dataset = dataset[folds_dict[str(fold)]['test']]

        train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
        test_loader = DataLoader(test_dataset, batch_size=batch_size)

        device = torch.device(device if torch.cuda.is_available() else 'cpu')

        model = GNN_graphpred(num_layer, emb_dim, num_tasks = 1, JK = JK, drop_ratio =dropout_ratio,feature_type = feature_type,
                              graph_pooling = graph_pooling, gnn_type = gnn_type).to(device)
        optimizer = torch.optim.Adam(model.parameters(), lr=lr,
                                     weight_decay=decay)
        

        test_best = 1e3
        for epoch in range(epochs):
            train_rmse = train()
            test_rmse = test(test_loader)
            if test_rmse<test_best:
                test_best = test_rmse
                
            print(f'Epoch: {epoch:03d}, Loss: {train_rmse:.4f}'
                  f'Test: {test_rmse:.4f} Test_best:{test_best:.4f}')
        best_result.append(test_best)
    print(f'datast_name:{dataset_name} BestResultOneSet:{best_result}')
    best_result_allset.append(best_result)
print('BestResultAllSet:',best_result_allset)

mglur2

{'name': 'mglur2', 'root': 'data', 'transform': None, 'pre_transform': <dataset.GenAtomFeatures object at 0x7f62dfe306a0>, 'pre_filter': None, '_indices': [14, 16, 23, 25, 9, 18, 21, 15, 7, 22, 0, 11, 24, 20, 2, 19, 6, 8, 3, 13, 5, 12, 4, 1, 17, 10], 'data': Data(x=[791, 115], edge_index=[2, 1734], edge_attr=[1734, 7], y=[26, 1], smiles=[26]), 'slices': defaultdict(<class 'dict'>, {'x': tensor([  0,  33,  54,  74, 102, 135, 169, 203, 230, 251, 285, 320, 348, 376,
        410, 444, 472, 506, 540, 576, 611, 632, 661, 695, 730, 764, 791]), 'edge_index': tensor([   0,   72,  118,  162,  224,  296,  370,  444,  504,  552,  626,  702,
         764,  826,  900,  974, 1036, 1110, 1184, 1262, 1338, 1386, 1450, 1524,
        1600, 1674, 1734]), 'edge_attr': tensor([   0,   72,  118,  162,  224,  296,  370,  444,  504,  552,  626,  702,
         764,  826,  900,  974, 1036, 1110, 1184, 1262, 1338, 1386, 1450, 1524,
        1600, 1674, 1734]), 'y': tensor([ 0,  1,  2,  3,  4,  5,  6,  7,  

In [ ]:
import torch
import json
import os.path as osp
from math import sqrt
import numpy as np

import torch
import torch.nn.functional as F
from rdkit import Chem

from torch_geometric.loader import DataLoader
from torch_geometric.datasets import MoleculeNet
from torch_geometric.nn.models import AttentiveFP

import os
import os.path as osp
import re

import torch
import torch.nn.functional as F
from rdkit import Chem
from torch_geometric.data import (InMemoryDataset, Data, download_url,
                                  extract_gz)
from torch_geometric.loader import DataLoader
from torch_geometric.datasets import MoleculeNet
from torch_geometric.nn.models import AttentiveFP

from model import GNN,GNN_graphpred
from dataset import LSSInhibitor,GenAtomFeatures,GenAttentiveFeatures
from loss import ada_batch_all_triplet_loss
from splitters import scaffold_split, random_split, random_scaffold_split, cv_random_split


device = 'cuda:7'
batch_size = 16
epochs = 200
lr = 0.0001
decay = 1e-3
num_layer = 5
emb_dim = 300
dropout_ratio = 0
JK = 'last'
dataset = 'EAAT3'
output_model_file = ''
gnn_type = 'gin'
seed = 0
num_workers = 8
mode = 'ada_batch_all_triplet_loss'   #ada_batch_all_triplet_loss,ada_batch_hard_triplet_loss,triplet_loss
feature_type = 'custom'  #random,onehot,custom,pseudo
graph_pooling = 'set2set2' #mean,last,sum,set2set,atention
cliff_list = [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0, 1.1, 1.2, 1.3, 1.4, 1.5, 1.6, 1.7, 1.8, 1.9, 
 2.0, 2.1, 2.2, 2.3, 2.4, 2.5, 2.6, 2.7, 2.8, 2.9, 3.0]

def train():
    total_loss = total_examples = 0
    for data in train_loader:
        data = data.to(device)
        optimizer.zero_grad()
        '''
        data.x = data.x.to(torch.float32)
        data.edge_index=data.edge_index.to(torch.long)
        data.edge_attr=data.edge_attr.to(torch.float32)
        data.batch=data.batch.to(torch.long)
        '''
        #out = model(float(data.x), data.edge_index.to(torch.long), data.edge_attr.to(torch.float32), data.batch.to(torch.long))
        emb,pre = model(data.x, data.edge_index, data.edge_attr, data.batch)

        #loss = F.mse_loss(out, data.y)
        loss = ada_batch_all_triplet_loss(embeddings=emb, labels=data.y, prediction=pre, device=device, minv=minv, maxv=maxv, weight=0.5, cliff=cliff,squared=False)
        loss.backward()
        optimizer.step()
        total_loss += float(loss) * data.num_graphs
        total_examples += data.num_graphs
    return sqrt(total_loss / total_examples)


@torch.no_grad()
def test(loader):
    mse = []
    for data in loader:
        data = data.to(device)
        emb,pre = model(data.x.to(torch.float32), data.edge_index, data.edge_attr, data.batch)
        pre = pre*(maxv-minv)+minv
        mse.append(F.mse_loss(pre, data.y, reduction='none').cpu())
        #print('mse:',mse)
    return float(torch.cat(mse, dim=0).mean().sqrt())

best_allcliff_allset = {}
for cliff in cliff_list:
    best_result_allset = []
    for dataset_name in LSSInhibitor.names.keys():

        print(dataset_name + "\n")
        path = './data'

        # use the attentiveFP node and edge features during the mol-2-graph transoformation
        dataset = LSSInhibitor(path, name=dataset_name, pre_transform=GenAtomFeatures('custom')).shuffle()
        #dataset = LSSInhibitor(path, name=dataset_name, pre_transform=GenAttentiveFeatures()).shuffle()
        #dataset = MoleculeNet(path, name='FreeSolv', pre_transform=GenFeatures()).shuffle()
        print(dataset.__dict__)

        #get min&max for normalization
        minv = 1e12
        maxv = -1e12
        for i in dataset:
            if i.y<minv:
                minv = i.y.item()
            if i.y>maxv:
                maxv = i.y.item()
        print(f'minv:{minv}  maxv:{maxv}') 


        # cross validation splitting
        cv_random_split(dataset, data_name = dataset_name, fold_idx = 0, frac_train=0.8, frac_valid=0.2, seed=0,smiles_list=None)
        if os.path.isfile(dataset_name+'_split_folds.json'):
            with open(dataset_name+"_split_folds.json","r") as f:
                folds_dict = json.load(f)
                print('FOLDS_dict:',folds_dict)
        '''
        N = len(dataset) // 5
        val_dataset = dataset[:N]
        test_dataset = dataset[N:2 * N]
        train_dataset = dataset[2 * N:]
        '''
        best_result = []

        for fold in range(len(folds_dict)):

            train_dataset = dataset[folds_dict[str(fold)]['train']]
            test_dataset = dataset[folds_dict[str(fold)]['test']]

            train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
            test_loader = DataLoader(test_dataset, batch_size=batch_size)

            device = torch.device(device if torch.cuda.is_available() else 'cpu')

            model = GNN_graphpred(num_layer, emb_dim, num_tasks = 1, JK = JK, drop_ratio =dropout_ratio,feature_type = feature_type,
                                  graph_pooling = graph_pooling, gnn_type = gnn_type).to(device)
            optimizer = torch.optim.Adam(model.parameters(), lr=lr,
                                         weight_decay=decay)


            test_best = 1e3
            for epoch in range(epochs):
                train_rmse = train()
                test_rmse = test(test_loader)
                if test_rmse<test_best:
                    test_best = test_rmse

                print(f'Epoch: {epoch:03d}, Loss: {train_rmse:.4f}'
                      f'Test: {test_rmse:.4f} Test_best:{test_best:.4f}')
            best_result.append(test_best)
        print(f'datast_name:{dataset_name} BestResultOneSet:{best_result}')
        best_result_allset.append(best_result)
    print('BestResultAllSet:',best_result_allset)
    best_allcliff_allset[cliff]= best_result_allset
print(best_allcliff_allset)

mglur2

{'name': 'mglur2', 'root': 'data', 'transform': None, 'pre_transform': <dataset.GenAtomFeatures object at 0x7fec6f9eaa90>, 'pre_filter': None, '_indices': [23, 25, 10, 18, 4, 13, 15, 11, 2, 17, 7, 8, 19, 20, 12, 21, 14, 5, 0, 22, 1, 6, 24, 3, 9, 16], 'data': Data(x=[791, 115], edge_index=[2, 1734], edge_attr=[1734, 7], y=[26, 1], smiles=[26]), 'slices': defaultdict(<class 'dict'>, {'x': tensor([  0,  33,  54,  74, 102, 135, 169, 203, 230, 251, 285, 320, 348, 376,
        410, 444, 472, 506, 540, 576, 611, 632, 661, 695, 730, 764, 791]), 'edge_index': tensor([   0,   72,  118,  162,  224,  296,  370,  444,  504,  552,  626,  702,
         764,  826,  900,  974, 1036, 1110, 1184, 1262, 1338, 1386, 1450, 1524,
        1600, 1674, 1734]), 'edge_attr': tensor([   0,   72,  118,  162,  224,  296,  370,  444,  504,  552,  626,  702,
         764,  826,  900,  974, 1036, 1110, 1184, 1262, 1338, 1386, 1450, 1524,
        1600, 1674, 1734]), 'y': tensor([ 0,  1,  2,  3,  4,  5,  6,  7,  

In [3]:
k = 0
p = []
for i in range(1,31):
    p.append(float(0.1*i))
print(p)
cliff_list = [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0, 1.1, 1.2, 1.3, 1.4, 1.5, 1.6, 1.7, 1.8, 1.9, 
 2.0, 2.1, 2.2, 2.3, 2.4, 2.5, 2.6, 2.7, 2.8, 2.9, 3.0]

[0.1, 0.2, 0.30000000000000004, 0.4, 0.5, 0.6000000000000001, 0.7000000000000001, 0.8, 0.9, 1.0, 1.1, 1.2000000000000002, 1.3, 1.4000000000000001, 1.5, 1.6, 1.7000000000000002, 1.8, 1.9000000000000001, 2.0, 2.1, 2.2, 2.3000000000000003, 2.4000000000000004, 2.5, 2.6, 2.7, 2.8000000000000003, 2.9000000000000004, 3.0]
